## Описание проекта
Сервис по продаже автомобилей с пробегом «Не бит, не крашен» разрабатывает приложение
для привлечения новых клиентов. В нём можно быстро узнать рыночную стоимость своего автомобиля.
В вашем распоряжении исторические данные: технические характеристики, комплектации и цены автомобилей.

## Задача
Нужно построить модель для определения стоимости.


## Доп. требования
Заказчику важны:
 - качество предсказания;
 - скорость предсказания;
 - время обучения.

## Описание данных

Признаки
 - DateCrawled — дата скачивания анкеты из базы
 - VehicleType — тип автомобильного кузова
 - RegistrationYear — год регистрации автомобиля
 - Gearbox — тип коробки передач
 - Power — мощность (л. с.)
 - Model — модель автомобиля
 - Kilometer — пробег (км)
 - RegistrationMonth — месяц регистрации автомобиля
 - FuelType — тип топлива
 - Brand — марка автомобиля
 - NotRepaired — была машина в ремонте или нет
 - DateCreated — дата создания анкеты
 - NumberOfPictures — количество фотографий автомобиля
 - PostalCode — почтовый индекс владельца анкеты (пользователя)
 - LastSeen — дата последней активности пользователя

Целевой признак
 - Price — цена (евро)

In [1]:
import numpy as np
import pandas as pd
import pandas_profiling

import plotly.express as px

from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error as mse
# немного экспериментальной магии от sklearn
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer

import catboost
import lightgbm as lgb


Шаг 1. Загрузим и посмотрим на данные

In [2]:
data = pd.read_csv('https://code.s3.yandex.net/datasets/autos.csv')
data.name = 'Cars'
data.sample(5)

DateCrawled  Price VehicleType  RegistrationYear Gearbox  \
264553  2016-03-20 09:39:16    250       wagon              1998  manual   
144624  2016-03-14 10:52:15   1000       sedan              1997    auto   
198022  2016-03-26 15:49:40    900       small              1998  manual   
183023  2016-03-26 18:55:53   3799         NaN              2004     NaN   
18309   2016-03-19 16:53:05   1600       sedan              1995  manual   

        Power   Model  Kilometer  RegistrationMonth FuelType Brand  \
264553     90  escort     150000                  4   petrol  ford   
144624    136  vectra     150000                 12   petrol  opel   
198022     65   corsa     150000                  8   petrol  opel   
183023      0  fusion     125000                  9      NaN  ford   
18309     101      a4     150000                 10   petrol  audi   

       NotRepaired          DateCreated  NumberOfPictures  PostalCode  \
264553         NaN  2016-03-20 00:00:00                 0       29593   
144624          no  2016-03-14 00:00:00                 0       42859   
198022          no  2016-03-26 00:00:00                 0       71332   
183023         NaN  2016-03-26 00:00:00                 0       41469   
18309          NaN  2016-03-19 00:00:00                 0       27478   

                   LastSeen  
264553  2016-04-06 04:44:43  
144624  2016-04-03 11:47:52  
198022  2016-04-06 04:15:40  
183023  2016-03-28 08:15:40  
18309   2016-04-05 00:15:41

Данные загружены, видим, что в данных присутствуют пропуски.

In [3]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 354369 entries, 0 to 354368
Data columns (total 16 columns):
 #   Column             Non-Null Count   Dtype 
---  ------             --------------   ----- 
 0   DateCrawled        354369 non-null  object
 1   Price              354369 non-null  int64 
 2   VehicleType        316879 non-null  object
 3   RegistrationYear   354369 non-null  int64 
 4   Gearbox            334536 non-null  object
 5   Power              354369 non-null  int64 
 6   Model              334664 non-null  object
 7   Kilometer          354369 non-null  int64 
 8   RegistrationMonth  354369 non-null  int64 
 9   FuelType           321474 non-null  object
 10  Brand              354369 non-null  object
 11  NotRepaired        283215 non-null  object
 12  DateCreated        354369 non-null  object
 13  NumberOfPictures   354369 non-null  int64 
 14  PostalCode         354369 non-null  int64 
 15  LastSeen           354369 non-null  object
dtypes: int64(7), object(

Датасет содержит 16 колонок и 354369 записей. 7 колонок int64 и 9 object колонок. Посмотрим, что по пропускам.

In [4]:
# проверим датасет на пропуски
def get_missing_values(data: pd.DataFrame) -> None:
    """
    Выводит данные о пропусках в колонках по датафрейму.
    Не изменяет данные внутри датафрейма.

    :param data: pd.DataFrame
    :return: None
    """
    # получаем имена колонок датафрейма
    columns = data.columns.to_list()
    data_len = len(data)
    # объявляем счетчик
    counter = -1
    print('='*60)
    # если есть пропуски в данных - выводим информацию о пропусках по колонкам
    if sum(data.isnull().sum()) > 0:
        print(f'Количество записей в датафрейме {data.name}: {data_len} \n')
        print(f'В датафрейме {data.name} имеются следующие пропуски:')
        for i in data.isnull().sum():
            counter += 1
            if i > 0:
                print(f'  - в колонке {columns[counter]}: {i} пропусков, это {i/data_len:0.2%} об общего объема данных')
    else:
        print(f'Отлично, в датафрейме {data.name} отсутствуют пропуски.')

# посмотрим на пропуски в данных
get_missing_values(data)

Количество записей в датафрейме Cars: 354369 

В датафрейме Cars имеются следующие пропуски:
  - в колонке VehicleType: 37490 пропусков, это 10.58% об общего объема данных
  - в колонке Gearbox: 19833 пропусков, это 5.60% об общего объема данных
  - в колонке Model: 19705 пропусков, это 5.56% об общего объема данных
  - в колонке FuelType: 32895 пропусков, это 9.28% об общего объема данных
  - в колонке NotRepaired: 71154 пропусков, это 20.08% об общего объема данных


Имеем 5 колонок с достаточно большим количеством пропусков.

In [5]:
data.head()

DateCrawled  Price VehicleType  RegistrationYear Gearbox  Power  \
0  2016-03-24 11:52:17    480         NaN              1993  manual      0   
1  2016-03-24 10:58:45  18300       coupe              2011  manual    190   
2  2016-03-14 12:52:21   9800         suv              2004    auto    163   
3  2016-03-17 16:54:04   1500       small              2001  manual     75   
4  2016-03-31 17:25:20   3600       small              2008  manual     69   

   Model  Kilometer  RegistrationMonth  FuelType       Brand NotRepaired  \
0   golf     150000                  0    petrol  volkswagen         NaN   
1    NaN     125000                  5  gasoline        audi         yes   
2  grand     125000                  8  gasoline        jeep         NaN   
3   golf     150000                  6    petrol  volkswagen          no   
4  fabia      90000                  7  gasoline       skoda          no   

           DateCreated  NumberOfPictures  PostalCode             LastSeen  
0  2016-03-24 00:00:00                 0       70435  2016-04-07 03:16:57  
1  2016-03-24 00:00:00                 0       66954  2016-04-07 01:46:50  
2  2016-03-14 00:00:00                 0       90480  2016-04-05 12:47:46  
3  2016-03-17 00:00:00                 0       91074  2016-03-17 17:40:17  
4  2016-03-31 00:00:00                 0       60437  2016-04-06 10:17:21

In [6]:
data['DateCrawled'] = pd.to_datetime(data['DateCrawled'], format='%Y-%m-%d %H:%M:%S')
data['DateCreated'] = pd.to_datetime(data['DateCreated'], format='%Y-%m-%d %H:%M:%S')
data_sorted = data.sort_values(by='DateCreated')

In [7]:
data_sorted

DateCrawled  Price  VehicleType  RegistrationYear Gearbox  \
61207  2016-03-16 11:48:06   8999          NaN              2005     NaN   
4001   2016-03-23 14:42:46   6000          bus              1995    auto   
342275 2016-03-05 21:44:26  10400          bus              1993     NaN   
86601  2016-04-02 19:47:40  14250  convertible              2005  manual   
175103 2016-03-08 17:57:45   5200  convertible              2006  manual   
...                    ...    ...          ...               ...     ...   
134418 2016-04-07 06:36:22     30        small              2000     NaN   
176987 2016-04-07 12:06:36   1800          NaN              2018  manual   
206303 2016-04-07 09:06:21   4300          bus              1998  manual   
309336 2016-04-07 06:36:21    500        wagon              1996     NaN   
305430 2016-04-07 08:36:21   1500        small              2003  manual   

        Power        Model  Kilometer  RegistrationMonth  FuelType  \
61207       0          147     125000                  0    petrol   
4001      200        other     150000                  0    petrol   
342275      0       ducato      30000                  1  gasoline   
86601     163          slk     150000                  6    petrol   
175103    109      2_reihe      80000                 11    petrol   
...       ...          ...        ...                ...       ...   
134418      0        corsa     150000                  9    petrol   
176987    150       spider     150000                  0       NaN   
206303    151  transporter     150000                  9  gasoline   
309336      0           a6     150000                  0    petrol   
305430     54        panda     150000                  7    petrol   

                Brand NotRepaired DateCreated  NumberOfPictures  PostalCode  \
61207      alfa_romeo         NaN  2014-03-10                 0       79669   
4001        chevrolet          no  2015-03-20                 0       24558   
342275           fiat         NaN  2015-06-18                 0       76275   
86601   mercedes_benz          no  2015-08-07                 0       76228   
175103        peugeot          no  2015-08-10                 0       26382   
...               ...         ...         ...               ...         ...   
134418           opel         NaN  2016-04-07                 0       88250   
176987     alfa_romeo          no  2016-04-07                 0       61184   
206303     volkswagen         NaN  2016-04-07                 0       65936   
309336           audi         yes  2016-04-07                 0       59348   
305430           fiat         NaN  2016-04-07                 0       28219   

                   LastSeen  
61207   2016-04-07 04:46:24  
4001    2016-04-07 03:45:01  
342275  2016-04-05 17:46:09  
86601   2016-04-07 09:15:23  
175103  2016-04-05 20:46:54  
...                     ...  
134418  2016-04-07 06:36:22  
176987  2016-04-07 12:25:20  
206303  2016-04-07 09:25:17  
309336  2016-04-07 06:36:21  
305430  2016-04-07 08:36:21  

[354369 rows x 16 columns]

In [8]:
pandas_profiling.ProfileReport(data_sorted)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [35]:
test = data[data['DateCreated'] > pd.to_datetime('2016-04-1', format='%Y-%m-%d')].drop(['DateCreated', 'DateCrawled', 'LastSeen', 'NumberOfPictures'], axis=1).dropna()
train = data.drop(data[data['DateCreated'] > pd.to_datetime('2016-04-1', format='%Y-%m-%d')].index).drop(['DateCreated', 'DateCrawled', 'LastSeen', 'NumberOfPictures'], axis=1).dropna()

features_train = train.drop('Price', axis=1)
target_train = train['Price']

test_features = test.drop('Price', axis=1)
test_target = test['Price']

In [15]:
impute_model = catboost.CatBoostClassifier(task_type='GPU', random_state=25, silent=True)
# ограничим количество итераций до 3 (чтобы на моем компе это выполнялось за разумное время :D, но чутка ухудшив качество дефолтно - 10)
# и заполнять будем от поля с наибольшим количеством пропусков к меньшему
it_imputer = IterativeImputer(impute_model, max_iter=6, imputation_order='descending')
data_after_imputer = it_imputer.fit_transform(features_train)

ValueError: could not convert string to float: 'small'

In [12]:
cbr = catboost.CatBoostRegressor(task_type='GPU', random_state=25, silent=True, nan_mode='Max')
cbr.fit(features_train, target_train, cat_features=['VehicleType','Gearbox','Model','FuelType','Brand','NotRepaired'])
pred = cbr.predict(test_features)
np.sqrt(mse(test_target, pred))

1713.0701551460945

In [33]:
features_train.columns

Index(['VehicleType', 'RegistrationYear', 'Gearbox', 'Power', 'Model',
       'Kilometer', 'RegistrationMonth', 'FuelType', 'Brand', 'NotRepaired',
       'PostalCode'],
      dtype='object')

In [36]:
features_train = pd.get_dummies(features_train, drop_first=True)
model = lgb.LGBMRegressor(random_state=25)
model.fit(features_train, target_train)
pred = model.predict(pd.get_dummies(test_features, drop_first=True))
np.sqrt(mse(test_target, pred))

ValueError: Number of features of the model must match the input. Model n_features_ is 306 and input n_features is 295